In [3]:
!pip install TensorFlow
!pip install Keras
!pip install pillow
!pip install NumPy
!Pip install tqdm

/bin/bash: line 1: Pip: command not found


In [4]:
from PIL import Image
import os
import string , numpy as np
from pickle import dump
from pickle import load
from tensorflow.keras.applications.xception import Xception #to get pre-trained model Xception
from tensorflow.keras.applications.xception import preprocess_input
# from keras.preprocessing.image import load_img
from tensorflow.keras.preprocessing.image import load_img

from tensorflow.keras.preprocessing.image import img_to_array
from tensorflow.keras.preprocessing.text import Tokenizer #for text tokenization
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import Input, Dense, add#Keras to build our CNN and LSTM
from tensorflow.keras.layers import LSTM, Embedding, Dropout
from tqdm.notebook import tqdm #to check loop progress
tqdm().pandas()
import re,string , pickle

0it [00:00, ?it/s]

In [5]:
def remove_punctuation(paragraph):

    translator = str.maketrans('', '', string.punctuation)
    # print(paragraph.translate(translator))
    paragraph = paragraph.replace('-' , ' ')
    # Replace words like "dog's" with "dog"
    text = re.sub(r"'s\b", '', paragraph)

    # Remove articles at the beginning of sentences
    text = re.sub(r'\b(a|an|the)\s', '', text, flags=re.IGNORECASE)
    return text.translate(translator)

In [6]:
def read_token_file(filename):
    file = open(filename , 'r')
    text_lines = file.readlines()
    return text_lines
    # It returns linewise text for further process

In [7]:
def make_caption_dict(description , image_info , data_dict):
    cleaned_description = []
    for word in description.split():
        if not word.isalnum() or word.isalpha():
            cleaned_description.append(word)
    single_discription_list = str(' '.join(cleaned_description))
    image_name, description_index = image_info.split('#')
    if image_name not in data_dict:
        data_dict[image_name] = []
    data_dict[image_name].append(single_discription_list)
#     print(data_dict)
    return data_dict

In [8]:
def text_2_vocab(final_dict):
    vocab = []
    for key in final_dict.keys():
        [vocab.append(d.split()) for d in final_dict[key]]
        return vocab

In [9]:
full_text_lines = read_token_file('/kaggle/input/flicker8k-image-captioning/Flickr8k_text/Flickr8k.token.txt')
print(len(full_text_lines))
data_dict = {}
for i,text_line in enumerate(full_text_lines[:20000]):
    parts = text_line.split('\t')
    image_info, description = parts[0], f"startseq {parts[1]} endseq"
    description = remove_punctuation(description.lower())
    temp_1 = make_caption_dict(description , image_info , data_dict)
#     final_vocabulary = text_2_vocab(cleaned_text_dictionary)

print(temp_1)
print(len(temp_1))

40460
{'1000268201_693b08cb0e.jpg': ['startseq child in pink dress is climbing up set of stairs in entry way endseq', 'startseq girl going into wooden building endseq', 'startseq little girl climbing into wooden playhouse endseq', 'startseq little girl climbing stairs to her playhouse endseq', 'startseq little girl in pink dress going into wooden cabin endseq'], '1001773457_577c3a7d70.jpg': ['startseq black dog and spotted dog are fighting endseq', 'startseq black dog and tri colored dog playing with each other on road endseq', 'startseq black dog and white dog with brown spots are staring at each other in street endseq', 'startseq two dogs of different breeds looking at each other on road endseq', 'startseq two dogs on pavement moving toward each other endseq'], '1002674143_1b742ab4b8.jpg': ['startseq little girl covered in paint sits in front of painted rainbow with her hands in bowl endseq', 'startseq little girl is sitting in front of large painted rainbow endseq', 'startseq small 

In [10]:
full_text_lines = read_token_file('/kaggle/input/flicker8k-image-captioning/Flickr8k_text/Flickr8k.token.txt')
print(len(full_text_lines))
data_dict = {}
for text_line in full_text_lines[20000:]:
    parts = text_line.split('\t')
    image_info, description = parts[0], f"startseq {parts[1]} endseq"
    description = remove_punctuation(description.lower())
    temp_2 = make_caption_dict(description , image_info , data_dict)
    # final_vocabulary = text_2_vocab(cleaned_text_dictionary)
print(temp_2)
print(len(temp_2))

40460
{'3094278545_febac56382.jpg': ['startseq bride folds her arms at beach endseq', 'startseq girl wears fancy dress and tiara endseq', 'startseq pretty girl wearing white dress dimond necklace and crown posing in front of beach endseq', 'startseq woman in white wearing tiara beach in background endseq', 'startseq woman wear fancy dress and tiara on beach endseq'], '309430053_cc58bcc36a.jpg': ['startseq boat floating on blue water endseq', 'startseq boat floats near someone swimming in clear blue water endseq', 'startseq person is swimming in crystal clear ocean water while his or her boat is anchored in background endseq', 'startseq person swims in shallow turquoise sea toward empty tethered rowboat endseq', 'startseq someone is swimming in ocean near unmanned rowboat endseq'], '3094317837_b31cbf969e.jpg': ['startseq man rides wave on surfboard endseq', 'startseq man wearing black wetsuit is surfing in water endseq', 'startseq person on surfboard riding wave endseq', 'startseq perso

In [11]:
temp_1.update(temp_2)
cleaned_caption_dictionary = temp_1
print(len(cleaned_caption_dictionary))

8092


In [12]:
all_caption_list = []
for single_caption in cleaned_caption_dictionary.values():
    all_caption_list.extend(single_caption)
print(all_caption_list)

['startseq child in pink dress is climbing up set of stairs in entry way endseq', 'startseq girl going into wooden building endseq', 'startseq little girl climbing into wooden playhouse endseq', 'startseq little girl climbing stairs to her playhouse endseq', 'startseq little girl in pink dress going into wooden cabin endseq', 'startseq black dog and spotted dog are fighting endseq', 'startseq black dog and tri colored dog playing with each other on road endseq', 'startseq black dog and white dog with brown spots are staring at each other in street endseq', 'startseq two dogs of different breeds looking at each other on road endseq', 'startseq two dogs on pavement moving toward each other endseq', 'startseq little girl covered in paint sits in front of painted rainbow with her hands in bowl endseq', 'startseq little girl is sitting in front of large painted rainbow endseq', 'startseq small girl in grass plays with fingerpaints in front of white canvas with rainbow on it endseq', 'starts

In [13]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(all_caption_list)

vocab_size = len(tokenizer.word_index)+1 #added extra one to consider OOV word

In [14]:
sequences = tokenizer.texts_to_sequences(all_caption_list)
print(sequences)

[[1, 40, 3, 87, 168, 5, 116, 48, 390, 10, 391, 3, 5128, 666, 2], [1, 17, 312, 61, 192, 114, 2], [1, 37, 17, 116, 61, 192, 2426, 2], [1, 37, 17, 116, 391, 18, 57, 2426, 2], [1, 37, 17, 3, 87, 168, 312, 61, 192, 2969, 2], [1, 13, 7, 6, 839, 7, 15, 339, 2], [1, 13, 7, 6, 1565, 231, 7, 31, 8, 134, 79, 4, 147, 2], [1, 13, 7, 6, 12, 7, 8, 25, 997, 15, 636, 20, 134, 79, 3, 69, 2], [1, 11, 28, 10, 737, 2643, 86, 20, 134, 79, 4, 147, 2], [1, 11, 28, 4, 724, 801, 317, 134, 79, 2], [1, 37, 17, 160, 3, 602, 103, 3, 45, 10, 590, 1188, 8, 57, 216, 3, 972, 2], [1, 37, 17, 5, 46, 3, 45, 10, 52, 590, 1188, 2], [1, 50, 17, 3, 38, 111, 8, 3406, 3, 45, 10, 12, 2427, 8, 1188, 4, 146, 2], [1, 185, 5, 17, 8, 1566, 46, 3, 45, 10, 1188, 768, 2], [1, 24, 17, 8, 1566, 768, 78, 3, 38, 2], [1, 9, 642, 4, 158, 32, 26, 7, 103, 51, 145, 2], [1, 9, 642, 4, 158, 18, 689, 12, 7, 5, 1263, 1492, 2], [1, 9, 616, 4, 158, 78, 8, 12, 6, 13, 7, 46, 83, 18, 145, 2], [1, 406, 9, 769, 4, 115, 158, 8, 26, 7, 2], [1, 9, 262, 4, 158

In [15]:
max_sequence_length = max([len(sequence) for sequence in sequences])
print("Max Sequence Length : " , max_sequence_length)
# sequences = pad_sequences(sequences,maxlen=max_sequence_lenght, padding='post')

# print(sequences)

Max Sequence Length :  34


91884032/91884032 [==============================] - 6s 0us/step
Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 299, 299, 3  0           []                               
                                )]                                                                
                                                                                                  
 block1_conv1 (Conv2D)          (None, 149, 149, 32  864         ['input_1[0][0]']                
                                )                                                                 
                                                                                                  
 block1_conv1_bn (BatchNormaliz  (None, 149, 149, 32  128        ['block1_conv1[0][0]']           
 ation)                      

In [45]:
# extracting image features
xception_model = Xception()
xception_model = Model(inputs=model.inputs ,outputs=model.layers[-2].output)

def img_to_vecFeature(image_path,xception_model):
    single_image = load_img(image_path ,target_size=(299,299,3))
    single_image = img_to_array(single_image)
    single_image = single_image.reshape((1,299,299,3))
    single_image = preprocess_input(single_image)
    feature = xception_model.predict(single_image)
    return feature

In [18]:
features = {}
image_directory = f"/kaggle/input/flicker8k-image-captioning/Flickr8k_Dataset/Flicker8k_Dataset"
for i in tqdm(os.listdir(image_directory)):
    image_path = os.path.join(image_directory,i)
    image_id = i.split('.')[0]
    feature = img_to_vecFeature(image_path)
    features[image_id] = feature

  0%|          | 0/8091 [00:00<?, ?it/s]

1/1 [==============================] - 0s 26ms/step


In [19]:
for key in list(features.keys()):
    new_key = key + ".jpg"
    features[new_key] = features.pop(key)
    
print(features)

{'3226254560_2f8ac147ea.jpg': array([[0.4664859 , 0.07270655, 0.        , ..., 0.36889115, 0.        ,
        0.        ]], dtype=float32), '214543992_ce6c0d9f9b.jpg': array([[0.11438929, 0.        , 0.21457443, ..., 0.20354354, 0.20359984,
        0.        ]], dtype=float32), '2366643786_9c9a830db8.jpg': array([[0.0000000e+00, 3.2443047e-01, 6.9061750e-01, ..., 0.0000000e+00,
        0.0000000e+00, 2.5590672e-04]], dtype=float32), '3368819708_0bfa0808f8.jpg': array([[0.3230384 , 0.        , 0.        , ..., 0.0039682 , 0.00885087,
        0.04604887]], dtype=float32), '2190227737_6e0bde2623.jpg': array([[0.02151563, 0.23933384, 0.05045644, ..., 0.58385384, 0.25094333,
        0.        ]], dtype=float32), '2752809449_632cd991b3.jpg': array([[1.2255326e-01, 1.8886034e-01, 0.0000000e+00, ..., 1.2803925e-04,
        1.7401660e-02, 0.0000000e+00]], dtype=float32), '3097776588_312932e438.jpg': array([[0.34567463, 0.04401206, 0.2520336 , ..., 0.00911178, 0.        ,
        0.        ]], 

In [20]:
pickle.dump(features, open('/kaggle/working/features.pkl', 'wb'))

In [21]:
# Model
ip1 = Input(shape = (2048, ))
fe1 = Dropout(0.2)(ip1)
fe2 = Dense(256, activation = 'relu')(fe1)
ip2 = Input(shape = (max_sequence_length, ))
se1 = Embedding(vocab_size, 200, mask_zero = True)(ip2)
se2 = Dropout(0.2)(se1)
se3 = LSTM(256)(se2)
decoder1 = add([fe2, se3])
decoder2 = Dense(256, activation = 'relu')(decoder1)
outputs = Dense(vocab_size, activation = 'softmax')(decoder2)
model = Model(inputs = [ip1, ip2], outputs = outputs)
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [26]:
#data generator, used by model.fit_generator()
def data_generator(descriptions, features, tokenizer, max_length):
    while 1:
        for key, description_list in descriptions.items():
            #retrieve photo features
            feature = features[key][0]
            input_image, input_sequence, output_word = create_sequences(tokenizer, max_length, description_list, feature)
            yield [[input_image, input_sequence], output_word]
def create_sequences(tokenizer, max_length, desc_list, feature):
    X1, X2, y = list(), list(), list()
    # walk through each description for the image
    for desc in desc_list:
        # encode the sequence
        seq = tokenizer.texts_to_sequences([desc])[0]
        # split one sequence into multiple X,y pairs
        for i in range(1, len(seq)):
            # split into input and output pair
            in_seq, out_seq = seq[:i], seq[i]
            # pad input sequence
            in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
            # encode output sequence
            out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
            # store
            X1.append(feature)
            X2.append(in_seq)
            y.append(out_seq)
    return np.array(X1), np.array(X2), np.array(y)

In [27]:
#load the data 
def load_photos(filename):
    with open(filename , 'r') as file:
        text = file.read()
    photos = text.split("\n")[:-1]
    return photos

def load_train_dictionary(photo_names,cleaned_discription):
    train_photo_list = {}
    
    for photo_name in photo_names:
        if photo_name in cleaned_discription:
            train_photo_list[photo_name] = cleaned_discription[photo_name]
    
    return train_photo_list

def load_features(photo_names, feature_dict):
    train_feature = {}
    
    for photo_name in photo_names:
        if photo_name in feature_dict:
            train_feature[photo_name] = feature_dict[photo_name]
    
    return train_feature

    
    

filename = "/kaggle/input/flicker8k-image-captioning/Flickr8k_text/Flickr_8k.trainImages.txt"

#train = loading_data(filename)
train_images = load_photos(filename)
# print(train_images)
train_descriptions = load_train_dictionary(train_images,cleaned_caption_dictionary)
train_features = load_features(train_images,features)

print(len(train_images))
print(len(train_descriptions))
print(len(train_features))

6000
6000
6000


In [28]:
steps = len(train_descriptions)
epochs = 10
for i in range(epochs):
    generator = data_generator(train_descriptions, train_features, tokenizer, max_sequence_length)
    model.fit_generator(generator, epochs=1, steps_per_epoch= steps, verbose=1)
    model.save("models/model_" + str(i) + ".h5")

/tmp/ipykernel_27/62525109.py:5: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  model.fit_generator(generator, epochs=1, steps_per_epoch= steps, verbose=1)


6000/6000 [==============================] - 662s 110ms/step - loss: 2.6115


In [48]:
def index_to_word(integer , tokenizer):
    for word, index in tokenizer.word_index.items():
        if index == integer:
            return word
    return None

def img_to_vecFeature(image_path,xception_model):
    single_image = load_img(image_path ,target_size=(299,299,3))
    single_image = img_to_array(single_image)
    single_image = single_image.reshape((1,299,299,3))
    single_image = preprocess_input(single_image)
    feature = xception_model.predict(single_image)
    return feature

In [46]:
def generate_desc(model,tokenizer,photo_feature,max_length):
    in_seq = 'startseq'
    for i in range(max_length):
        sequence = tokenizer.texts_to_sequences([in_seq])[0]
        sequence = pad_sequences([sequence], maxlen=max_length)
        prediction = model.predict([photo_feature,sequence],verbose = 0)
        prediction = np.argmax(prediction)
        current_word = index_to_word(prediction , tokenizer)
        if word == None:
            break
        in_seq += ' ' + word
        
        if word == 'endseq':
            break
    return in_seq

In [53]:
max_length = max_sequence_length
# tokenizer = load(open("tokenizer.p","rb"))

img_path = '/kaggle/input/flicker8k-image-captioning/Flickr8k_Dataset/Flicker8k_Dataset/111537222_07e56d5a30.jpg'
# '/kaggle/input/flicker8k-image-captioning/Flickr8k_Dataset/Flicker8k_Dataset/1003163366_44323f5815.jpg'

# extracting image features
xception_model = Xception()
xception_model = Model(inputs=model.inputs ,outputs=model.layers[-2].output)

model = load_model('/kaggle/working/models/model_9.h5')
print(model)
photo_feature = img_to_vecFeature(img_path,xception_model)
# img = Image.open(img_path)
description = generate_desc(model, tokenizer, photo_feature, max_length)
print("\n\n")
print(description)
plt.imshow(img)

ValueError: in user code:

    File "/opt/conda/lib/python3.10/site-packages/keras/engine/training.py", line 2169, in predict_function  *
        return step_function(self, iterator)
    File "/opt/conda/lib/python3.10/site-packages/keras/engine/training.py", line 2155, in step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    File "/opt/conda/lib/python3.10/site-packages/keras/engine/training.py", line 2143, in run_step  **
        outputs = model.predict_step(data)
    File "/opt/conda/lib/python3.10/site-packages/keras/engine/training.py", line 2111, in predict_step
        return self(x, training=False)
    File "/opt/conda/lib/python3.10/site-packages/keras/utils/traceback_utils.py", line 70, in error_handler
        raise e.with_traceback(filtered_tb) from None
    File "/opt/conda/lib/python3.10/site-packages/keras/engine/input_spec.py", line 219, in assert_input_compatibility
        raise ValueError(

    ValueError: Layer "model_18" expe